In [1]:
from datasets import load_dataset

dataset = load_dataset("dair-ai/emotion")
dataset

No config specified, defaulting to: emotion/split
Reusing dataset emotion (/root/.cache/huggingface/datasets/dair-ai___emotion/split/1.0.0/cca5efe2dfeb58c1d098e0f9eeb200e9927d889b5a03c67097275dfb5fe463bd)


  0%|          | 0/3 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 16000
    })
    validation: Dataset({
        features: ['text', 'label'],
        num_rows: 2000
    })
    test: Dataset({
        features: ['text', 'label'],
        num_rows: 2000
    })
})

In [3]:
import pandas as pd

dataset_train = dataset['train'].to_pandas()
dataset_test = dataset['test'].to_pandas()

complete_dataset = pd.concat([dataset_train, dataset_test])

complete_dataset.info()
complete_dataset.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 18000 entries, 0 to 1999
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   text    18000 non-null  object
 1   label   18000 non-null  int64 
dtypes: int64(1), object(1)
memory usage: 421.9+ KB


text  label
0                            i didnt feel humiliated      0
1  i can go from feeling so hopeless to so damned...      0
2   im grabbing a minute to post i feel greedy wrong      3
3  i am ever feeling nostalgic about the fireplac...      2
4                               i am feeling grouchy      3

In [4]:
# imports for model creation
import tensorflow as tf
from keras import layers
from keras import losses
import keras
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [5]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(complete_dataset['text'])

vocab_size = len(tokenizer.word_index) + 1
max_length = 200    # max words in a sentence
embedding_dim = 50    # TODO: need to adjust accordingly

X_train = tokenizer.texts_to_sequences(dataset_train['text'])
X_train = pad_sequences(X_train, maxlen=max_length, padding='post')

X_test = tokenizer.texts_to_sequences(dataset_test['text'])
X_test = pad_sequences(X_test, maxlen=max_length, padding='post')

y_train = dataset_train['label']
y_test = dataset_test['label']

from keras.utils import to_categorical

num_classes = 6  # Assuming you have 3 classes
y_train_encoded = to_categorical(y_train, num_classes=num_classes)
y_test_encoded = to_categorical(y_test, num_classes=num_classes)

In [6]:
labels = complete_dataset['label']

print(X_train.shape)
print(X_test.shape)
print(y_train.shape)
print(y_test.shape)

(16000, 200)
(2000, 200)
(16000,)
(2000,)


In [7]:
# Build the model
model = keras.Sequential([
  keras.layers.Embedding(input_dim=vocab_size, output_dim=embedding_dim, input_shape=(max_length,)),
  keras.layers.GlobalAveragePooling1D(),
  keras.layers.Dense(32, activation='relu'),
  keras.layers.Dense(6, activation='sigmoid')
])

In [8]:
# Compile the model
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

In [9]:
# split the dataset into train and test
# from sklearn.model_selection import train_test_split

# X_train, X_test, y_train, y_test = train_test_split(, labels, test_size=0.3, random_state=42, shuffle=True)
# X_train

In [12]:
# train the model
model.fit(X_train, y_train_encoded, epochs=15, batch_size=32, validation_data=(X_test, y_test_encoded))

Epoch 1/15


2024-03-31 14:12:18.969565: E tensorflow/stream_executor/cuda/cuda_blas.cc:232] failed to create cublas handle: CUBLAS_STATUS_NOT_INITIALIZED
2024-03-31 14:12:18.969636: E tensorflow/stream_executor/cuda/cuda_blas.cc:234] Failure to initialize cublas may be due to OOM (cublas needs some free memory when you initialize it, and your deep-learning framework may have preallocated more than its fair share), or may be because this binary was not built with support for the GPU in your machine.
2024-03-31 14:12:18.969674: W tensorflow/core/framework/op_kernel.cc:1745] OP_REQUIRES failed at matmul_op_impl.h:438 : INTERNAL: Attempting to perform BLAS operation using StreamExecutor without BLAS support


InternalError: Graph execution error:

Detected at node 'sequential/dense/MatMul' defined at (most recent call last):
    File "/usr/lib/python3.9/runpy.py", line 197, in _run_module_as_main
      return _run_code(code, main_globals, None,
    File "/usr/lib/python3.9/runpy.py", line 87, in _run_code
      exec(code, run_globals)
    File "/usr/local/lib/python3.9/dist-packages/ipykernel_launcher.py", line 17, in <module>
      app.launch_new_instance()
    File "/usr/local/lib/python3.9/dist-packages/traitlets/config/application.py", line 1041, in launch_instance
      app.start()
    File "/usr/local/lib/python3.9/dist-packages/ipykernel/kernelapp.py", line 712, in start
      self.io_loop.start()
    File "/usr/local/lib/python3.9/dist-packages/tornado/platform/asyncio.py", line 199, in start
      self.asyncio_loop.run_forever()
    File "/usr/lib/python3.9/asyncio/base_events.py", line 601, in run_forever
      self._run_once()
    File "/usr/lib/python3.9/asyncio/base_events.py",

In [48]:
# Evaluate the model
loss, accuracy = model.evaluate(X_test, y_test_encoded)
accuracy

63/63 [==============================] - 0s 2ms/step - loss: 0.5242 - accuracy: 0.8580


0.8579999804496765